In [42]:
# Model design
import agentpy as ap
import random

# Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import IPython


In [43]:
# If agentpy is not installed, uncomment this
# ! pip install agentpy

In [44]:

'''
Rules of the system:
1. A burning tree becomes an empty site
2. A green tree becomes burning if at least one of its neighbours is burning
3. At an empty site, a tree grows with the probability p
4. A tree without a burning neighbour becomes a burning tree at any time step with the probability f ('lightning')

Modifications needed:
1. Do not automatically start the burning
2. Add a condition where a tree starts growing
3. Adjust probabilities
4. Do not stop the animation
Hello :)
'''

"\nRules of the system:\n1. A burning tree becomes an empty site\n2. A green tree becomes burning if at least one of its neighbours is burning\n3. At an empty site, a tree grows with the probability p\n4. A tree without a burning neighbour becomes a burning tree at any time step with the probability f ('lightning')\n\nModifications needed:\n1. Do not automatically start the burning\n2. Add a condition where a tree starts growing\n3. Adjust probabilities\n4. Do not stop the animation\nHello :)\n"

In [45]:
class ForestModel(ap.Model):

    def setup(self):

        # Create agents (trees)
        n_trees = int(self.p['Tree density'] * (self.p.size**2))
        trees = self.agents = ap.AgentList(self, n_trees)

        # Create grid (forest)
        self.forest = ap.Grid(self, [self.p.size]*2, track_empty=True)
        self.forest.add_agents(trees, random=True, empty=True)

        # Initiate a dynamic variable for all trees
        # Condition 0: Alive, 1: Burning, 2: Empty
        self.agents.condition = 0

        # Amount of lightning
        self.f = self.p['probability of lightning']

        # Ratio between f and p
        self.p_over_f = self.p['p_over_f']

        # Assign value to p
        self.growth = self.f * self.p_over_f

        # Start a fire from the left side of the grid
        # unfortunate_trees = self.forest.agents[0:self.p.size, 0:2]
        # unfortunate_trees.condition = 1
        #added:
        self.tree_counts = []  # Initialize list to store number of trees

    def step(self):

        # Select burning trees
        burning_trees = self.agents.select(self.agents.condition == 1)

        # Select empty lots
        no_trees = self.agents.select(self.agents.condition == 2)

        # Select healthy trees
        healthy_trees = self.agents.select(self.agents.condition == 0)

        # Add lighting
        for tree in healthy_trees:
            if random.random() < self.f:
                tree.condition = 1

        # Spread fire
        for tree in burning_trees:
            for neighbor in self.forest.neighbors(tree):
                if neighbor.condition == 0:
                    neighbor.condition = 1 # Neighbor starts burning
            tree.condition = 2 # Tree burns out
        nr_trees = len(self.agents.select(self.agents.condition == 0))
        self.tree_counts.append(nr_trees)  # Save number of trees at each step
        
        for tree in no_trees:
            if random.random() < self.growth:
                tree.condition = 0

        # Stop simulation if no fire is left
       # if len(burning_trees) == 0:
        #    self.stop()

    def end(self):

        # Document a measure at the end of the simulation
        burned_trees = len(self.agents.select(self.agents.condition == 2))
        self.report('Percentage of burned trees',
                    burned_trees / len(self.agents))

In [46]:
# Define parameters

parameters = {
    'Tree density': 0.5, # Percentage of grid covered by trees
    'size': 100, # Height and length of the grid
    'steps': 200,
    'probability of lightning': 0.0001,
    'p_over_f': 10000 # assign a ratio to ensure that f << p
}

In [47]:
# Create single-run animation with custom colors

def animation_plot(model, ax):
    attr_grid = model.forest.attr_grid('condition')
    color_dict = {0:'#7FC97F', 1:'#d62c2c', 2:'#e5e5e5', None:'#d5e5d5'}
    ap.gridplot(attr_grid, ax=ax, color_dict=color_dict, convert=True)
    ax.set_title(f"Simulation of a forest fire\n"
                 f"Time-step: {model.t}, Trees left: "
                 f"{len(model.agents.select(model.agents.condition == 0))}")

def animation_plot_values(model):
    time_steps = []
    attr_grid = model.forest.attr_grid('condition')
    model.tree_counts.append(len(model.agents.select(model.agents.condition == 0)))
    return time_steps, model.tree_counts


fig, ax = plt.subplots()
model = ForestModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)
IPython.display.HTML(animation.to_jshtml(fps=15))


c:\Users\rosam\anaconda3\envs\csp\Lib\site-packages\matplotlib\animation.py:908: UserWarning: Animation was deleted without rendering anything. This is most likely not intended. To prevent deletion, assign the Animation to a variable, e.g. `anim`, that exists until you output the Animation using `plt.show()` or `anim.save()`.
  warnings.warn(


In [48]:
# list_lightning = [0.0001, 0.001, 0.01, 0.1]
# list_new_tree = [0.01, 0.05, 0.1, 0.2]
# for f in list_lightning:
#     for p in list_new_tree:
#         parameters['probability of lightning'] = f
#         parameters['probability of new tree'] = p
#         model = ForestModel(parameters)
#         model.setup()  # initialize model

#         # run your simulation manually:
#         for step in range(parameters['steps']):
#             model.step()
#             trees = model.tree_counts
#             time = list(range(len(trees)))
    
#         print(trees)
#         print(time)
#         plt.plot(time, trees)
#         plt.xlabel("Time Step")
#         plt.ylabel("Number of Trees")
#         plt.title(f"probability of lightning: {f}, probability of new tree: {p}")
#         plt.grid(True)
#         plt.show()
